In [20]:
import pandas as pd
import numpy as np
import plotly
import datetime
import plotly.graph_objs as go

In [21]:
data = pd.read_csv("satcat.csv") 
# Preview the first 5 lines of the loaded data 
data.head()

OBJECT_NAME  OBJECT_ID  NORAD_CAT_ID OBJECT_TYPE OPS_STATUS_CODE OWNER  \
0    SL-1 R/B  1957-001A             1         R/B               D   CIS   
1   SPUTNIK 1  1957-001B             2         PAY               D   CIS   
2   SPUTNIK 2  1957-002A             3         PAY               D   CIS   
3  EXPLORER 1  1958-001A             4         PAY               D    US   
4  VANGUARD 1  1958-002B             5         PAY             NaN    US   

  LAUNCH_DATE LAUNCH_SITE  DECAY_DATE  PERIOD  INCLINATION  APOGEE  PERIGEE  \
0  1957-10-04       TYMSC  1957-12-01   96.19        65.10   938.0    214.0   
1  1957-10-04       TYMSC  1958-01-03   96.10        65.00  1080.0     64.0   
2  1957-11-03       TYMSC  1958-04-14  103.74        65.33  1659.0    211.0   
3  1958-02-01       AFETR  1970-03-31   88.48        33.15   215.0    183.0   
4  1958-03-17       AFETR         NaN  132.74        34.24  3833.0    650.0   

      RCS DATA_STATUS_CODE ORBIT_CENTER ORBIT_TYPE  
0  20.420              NaN           EA        IMP  
1     NaN              NaN           EA        IMP  
2   0.080              NaN           EA        IMP  
3     NaN              NaN           EA        IMP  
4   0.122              NaN           EA        ORB

In [22]:
data = pd.read_csv("iceye.csv") 
# Preview the first 5 lines of the loaded data 
data

OBJECT_NAME   OBJECT_ID                       EPOCH  MEAN_MOTION  \
0              ICEYE-X1   2018-004D  2021-05-29T18:30:20.328768    15.244479   
1              ICEYE-X2  2018-099AU  2021-05-29T20:41:31.375680    14.955381   
2  HARBINGER (ICEYE-X3)   2019-026E  2021-05-29T10:31:13.189440    15.219809   
3              ICEYE-X5   2019-038C  2021-05-29T18:00:30.849984    14.970357   
4              ICEYE-X4   2019-038D  2021-05-29T17:40:47.594208    14.969496   
5              ICEYE-X7   2020-068L  2021-05-29T11:23:20.294880    15.009617   
6              ICEYE-X6   2020-068M  2021-05-29T14:03:23.580576    15.009123   
7              ICEYE-X9  2021-006CX  2021-05-29T18:09:06.657120    15.123328   
8              ICEYE-X8  2021-006DB  2021-05-29T18:30:39.697920    15.121413   

   ECCENTRICITY  INCLINATION  RA_OF_ASC_NODE  ARG_OF_PERICENTER  MEAN_ANOMALY  \
0      0.000790      97.4052        222.5253           262.8436       97.1904   
1      0.001577      97.6659        220.8512           107.0709      253.2249   
2      0.000620      40.0183        131.7420            78.1279      282.0217   
3      0.002244      97.7779        114.6345            73.2633      287.1055   
4      0.002263      97.7756        114.4574            74.4397      285.9308   
5      0.002012      97.6859         86.7651           133.5622      226.7240   
6      0.001826      97.6950         86.6708           150.0733      210.1417   
7      0.001018      97.4934        211.2613           160.3281      343.0290   
8      0.000930      97.4909        211.1810           159.6477      337.3664   

   EPHEMERIS_TYPE CLASSIFICATION_TYPE  NORAD_CAT_ID  ELEMENT_SET_NO  \
0               0                   U         43114             999   
1               0                   U         43800             999   
2               0                   U         44229             999   
3               0                   U         44389             999   
4               0                   U         44390             999   
5               0                   U         46496             999   
6               0                   U         46497             999   
7               0                   U         47506             999   
8               0                   U         47510             999   

   REV_AT_EPOCH         BSTAR  MEAN_MOTION_DOT  MEAN_MOTION_DDOT  
0         18773  6.355200e-05     1.489000e-05                 0  
1         13569  4.608800e-06    -6.000000e-08                 0  
2         11494  3.754800e-05     6.910000e-06                 0  
3         10386 -6.966800e-07    -6.800000e-07                 0  
4         10386  6.461300e-05     6.860000e-06                 0  
5          3646  2.428200e-04     3.049000e-05                 0  
6          3646 -1.140100e-04    -1.517000e-05                 0  
7          1921  5.047000e-05     8.110000e-06                 0  
8          1921  8.150500e-05     1.342000e-05                 0

In [23]:
from skyfield.api import load, EarthSatellite

ts = load.timescale()
t = ts.now()
satellites = load.tle_file("full_catalog.txt")
# satellites = load.tle_file("iceye.txt")
print('Loaded', len(satellites), 'satellites\n')

Loaded 21584 satellites



In [27]:
x_pos, y_pos, z_pos = [], [], []

start = datetime.datetime.now()
for i, sat in enumerate(satellites):
    geocentric = sat.at(t)
    # print(100*i/len(satellites), '%', sat, end='\r')
    [x.append(y) for x,y in zip([x_pos, y_pos, z_pos], geocentric.position.km)]
datetime.datetime.now() - start

datetime.timedelta(seconds=6, microseconds=730171)

In [28]:
# Configure Plotly to be rendered inline in the notebook.
plotly.offline.init_notebook_mode()

# Configure the trace.
trace = go.Scatter3d(
    x=x_pos,  # <-- Put your data instead
    y=y_pos,  # <-- Put your data instead
    z=z_pos,  # <-- Put your data instead
    mode='markers',
    marker={
        'size': 1,
        'opacity': 0.8,
    }
)

earth_radius = 12756/2

# Set up 100 points. First, do angles
theta = np.linspace(0,2*np.pi,100)
phi = np.linspace(0,np.pi,100)

# Set up coordinates for points on the sphere
x0 = earth_radius * np.outer(np.cos(theta),np.sin(phi))
y0 = earth_radius * np.outer(np.sin(theta),np.sin(phi))
z0 = earth_radius * np.outer(np.ones(100),np.cos(phi))

# Set up trace
earth_trace = go.Surface(x=x0, y=y0, z=z0, colorscale=[[0, '#32ff5b'], [1, '#32ff5b']])
earth_trace.update(showscale=False)

# Configure the layout.
layout = go.Layout(
    margin={'l': 0, 'r': 0, 'b': 0, 't': 0},
    paper_bgcolor='rgba(30,30,30,255)',
    plot_bgcolor='rgba(255,255,255,255)'
    # paper_bgcolor='rgba(30,30,30,255)',
    # plot_bgcolor='rgba(0,0,0,0)'
)

data = [trace, earth_trace]

plot_figure = go.Figure(data=data, layout=layout)
plot_figure.update_layout(font_color="white")

# plot_figure.update_layout(yaxis=dict(color='#E00'))

# Render the plot.
plotly.offline.iplot(plot_figure)